In [1]:
import pandas as pd
import numpy as np
import altair as alt

In [2]:
df = pd.read_csv("predictive_maintenance.csv")

In [3]:
df.head(10)

UDI Product ID Type  Air temperature [K]  Process temperature [K]  \
0    1     M14860    M                298.1                    308.6   
1    2     L47181    L                298.2                    308.7   
2    3     L47182    L                298.1                    308.5   
3    4     L47183    L                298.2                    308.6   
4    5     L47184    L                298.2                    308.7   
5    6     M14865    M                298.1                    308.6   
6    7     L47186    L                298.1                    308.6   
7    8     L47187    L                298.1                    308.6   
8    9     M14868    M                298.3                    308.7   
9   10     M14869    M                298.5                    309.0   

   Rotational speed [rpm]  Torque [Nm]  Tool wear [min]  Target Failure Type  
0                    1551         42.8                0       0   No Failure  
1                    1408         46.3                3       0   No Failure  
2                    1498         49.4                5       0   No Failure  
3                    1433         39.5                7       0   No Failure  
4                    1408         40.0                9       0   No Failure  
5                    1425         41.9               11       0   No Failure  
6                    1558         42.4               14       0   No Failure  
7                    1527         40.2               16       0   No Failure  
8                    1667         28.6               18       0   No Failure  
9                    1741         28.0               21       0   No Failure

### 1. Зависимость износа инcтрумента (tool wear) и тип неисправности (Failure Type)

In [4]:
df= df.rename(columns={"Air temperature [K]": "Air Temp", "Process temperature [K]": "Process Temp", "Rotational speed [rpm]": "Rotational Speed", "Torque [Nm]":"Torque", "Tool wear [min]":"Tool wear"})

In [5]:
df.head(5)

UDI Product ID Type  Air Temp  Process Temp  Rotational Speed  Torque  \
0    1     M14860    M     298.1         308.6              1551    42.8   
1    2     L47181    L     298.2         308.7              1408    46.3   
2    3     L47182    L     298.1         308.5              1498    49.4   
3    4     L47183    L     298.2         308.6              1433    39.5   
4    5     L47184    L     298.2         308.7              1408    40.0   

   Tool wear  Target Failure Type  
0          0       0   No Failure  
1          3       0   No Failure  
2          5       0   No Failure  
3          7       0   No Failure  
4          9       0   No Failure

In [17]:
alt.data_transformers.enable('vegafusion')

color_scale = alt.Scale(
    domain=['L', 'M', 'H'],
    range=['blue', 'green', 'red']
)

chart = alt.Chart(df).mark_circle(opacity=0.4).encode(
    x=alt.X('Tool wear:Q', title='Износ инструмента'),
    y=alt.Y('Failure Type:N', title='Тип сбоя'),
    color=alt.Color('Type:N', 
                   scale=color_scale,
                   legend=alt.Legend(title='Type')),
    tooltip=['Tool wear', 'Failure Type', 'Type']
).properties(
    width=600,
    height=400,
    title='Зависимость износа инструмента от типа поломки'
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
)

chart

alt.Chart(...)

### 2. Гистограмма износа инструмента

In [18]:
chart = alt.Chart(df).mark_bar().encode(
    alt.X('Tool wear:Q', bin=alt.Bin(maxbins=30), title='Износ инструмента'),
    alt.Y('count():Q', title='Частота'), 
).properties(
    title='Гистограмма износа инструмента',
    width=600,
    height=400
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_title(
    fontSize=16
)

chart.configure_view(
    stroke=None
).show()

alt.Chart(...)

### 3. График плотности для Torque

In [19]:
chart = alt.Chart(df).transform_density(
    'Torque', as_=['Torque', 'density'], bandwidth=1
).mark_area(
    interpolate='basis',
    fill='skyblue',
    opacity=0.6
).encode(
    alt.X('Torque:Q', title='Частота'),
    alt.Y('density:Q', title='Плотность')
).properties(
    title='График плотности "Частоты"',
    width=600,
    height=400
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_title(
    fontSize=16
)

chart.configure_view(
    stroke=None
).show()


alt.Chart(...)

### 4. Зависимость Процессной температуры (process temperature) и частоты вращения (rotational speed):

In [20]:
chart = alt.Chart(df).mark_circle().encode(
    alt.X('Process Temp:Q', title='Температура процесса [K]'),
    alt.Y('Rotational Speed:Q', title='скорость вращения [rpm]'),
    alt.Size('Tool wear:Q', scale=alt.Scale(range=[1000, 1000]), title='Износ инструмента'),  # Увеличен диапазон размера
    alt.Color('Tool wear:Q', scale=alt.Scale(scheme='viridis'), title='Износ инструмента'),
    tooltip=['Process Temp', 'Rotational Speed', 'Tool wear']
).properties(
    title='Пузырьковая диаграмма: Зависимость температуры процесса от скорости вращения',
    width=300,
    height=400
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_title(
    fontSize=16
)

chart.configure_view(
    stroke=None
).show()


alt.Chart(...)

### 5.Диаграмма размаха зависимости типа неисправности (Failure Type) от Крутящего моммента (Torque) 

In [21]:
chart = alt.Chart(df).mark_boxplot().encode(
    alt.X('Failure Type:N', title='Тип сбоя'),
    alt.Y('Torque:Q', title='Крутящий момент'),
).properties(
    title='Диаграмма размаха крутящего момента по типам неисправностей',
    width=800,
    height=400
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_title(
    fontSize=16
)

chart.configure_view(
    stroke=None
).show()


alt.Chart(...)

### 6.Линейный график зависимости типа неисправности (Failure Type) от Крутящего моммента (Torque) 

In [22]:
chart = alt.Chart(df).mark_line(point=True).encode(
    alt.X('Failure Type:N', title='Тип неисправности'),
    alt.Y('Torque:Q', title='Крутящий момент'),
    color='Failure Type:N'
).properties(
    title='Линейный график крутящего момента по типам неисправностей',
    width=1000,
    height=1000
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_title(
    fontSize=16
)

chart.configure_view(
    stroke=None
).show()


alt.Chart(...)

### 7.Линейный график зависимости изменения температуры воздуха [K] по "UDI":

In [23]:
chart = alt.Chart(df).mark_line(color='green').encode(
    alt.X('UDI:Q', title='Номер идентификатора'),
    alt.Y('Air Temp:Q', title='Температура процесса [K]')
).properties(
    title='Изменение температуры процесса [K] по номеру идентификатора',
    width=4000,
    height=2000
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_title(
    fontSize=16
)

chart.configure_view(
    stroke=None
).show()


alt.Chart(...)

## 8.Диаграмма рассеяния с регрессионной линией

In [13]:
scatter = alt.Chart(df).mark_circle(size=50, color='blue').encode(
    alt.X('Air Temp:Q', title='Температура воздуха (°C)'),
    alt.Y('Tool wear:Q', title='Износ инструмента (мм)')
)

line = alt.Chart(df).mark_line(color='red', strokeDash=[5, 5]).encode(
    alt.X('Air Temp:Q'),
    alt.Y('Tool wear:Q')
)

annotations = alt.Chart(df).mark_text(
    align='left',
    baseline='middle',
    dx=5,
    dy=5
).encode(
    alt.X('Air Temp:Q'),
    alt.Y('Tool wear:Q'),
    text=alt.Text('Tool wear:Q', format='.2f')
)

chart = scatter + line + annotations

chart.properties(
    title='Зависимость износа инструмента от температуры воздуха',
    width=1000,
    height=1000
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_title(
    fontSize=16
).configure_view(
    stroke=None
).show()


alt.LayerChart(...)

### 9.Диаграмма рассеивания: крутящий момент от скорости Вращения

In [14]:
chart = alt.Chart(df).mark_circle(size=100).encode(
    alt.X('Rotational Speed:Q', title='Скорость вращения (об/мин)'),
    alt.Y('Torque:Q', title='Крутящий момент (Нм)'),
    alt.Color('Type:N', title='Тип', scale=alt.Scale(scheme='set1')),
    tooltip=['Rotational Speed', 'Torque', 'Type']
).properties(
    title='Зависимость крутящего момента от скорости вращения',
    width=2000,
    height=1000
).configure_axis(
    labelFontSize=12,
    titleFontSize=14
).configure_title(
    fontSize=16
).configure_view(
    stroke=None
)

chart.show()


alt.Chart(...)